In [1]:
from urllib.request import urlopen
from urllib.error import HTTPError, URLError
from bs4 import BeautifulSoup
import pandas as pd
import time

def scrape_NBA_game_data(start_year=2011, end_year=2024):
    months = ["october", "november", "december", "january", "february", "march", "april"]
    final_df = pd.DataFrame(columns=["Date", "Start (ET)", "Visitor/Neutral", "Visitor PTS", "Home/Neutral", "Home PTS", "Attend.", "Arena", "Notes"])

    for year in range(start_year, end_year + 1):
        year_data_available = True
        for month in months:
            url = f"https://www.basketball-reference.com/leagues/NBA_{year}_games-{month}.html"
            try:
                html = urlopen(url)
                soup = BeautifulSoup(html, 'html.parser')
                table = soup.find('table', {'id': 'schedule'})
                if not table:  # If the table is not found, skip the year
                    year_data_available = False
                    break

                rows = table.find_all('tr')
                for row in rows[1:]:  # Skip the header row
                    cols = row.find_all(['th', 'td'])
                    if cols:
                        data = [ele.get_text() for ele in cols]
                        if len(data) >= 10:  # Ensure data list has enough elements
                            # Map data to corresponding columns based on the provided structure
                            data_dict = {
                                "Date": data[0],
                                "Start (ET)": data[1],
                                "Visitor/Neutral": data[2],
                                "Visitor PTS": data[3],
                                "Home/Neutral": data[4],
                                "Home PTS": data[5],
                                "Attend.": data[8] ,
                                "Arena": data[9] ,
                                "Notes": data[10] if len(data) > 10 else ''
                            }
                            final_df = final_df.append(data_dict, ignore_index=True)
                        else:
                            # Print a message if a row with insufficient data is found
                            print(f"Skipping row with insufficient data: {data}")
            except (HTTPError, URLError) as e:
                # If a rate limit HTTP error is encountered, wait and retry
                if e.code == 429:
                    print("Rate limit hit. Waiting to retry...")
                    time.sleep(60)  # Wait for 60 seconds before retrying
                    continue
                else:
                    print(f"HTTP Error {e.code}: {e.reason}")
                    year_data_available = False
                    break

            time.sleep(3)  # Delay between requests to be polite to the server

        if not year_data_available:
            print(f"Data not available for all months in {year}. Skipping year.")

    final_df.to_csv("scores.csv", index=False)
    return final_df

# Example usage:
data = scrape_NBA_game_data()

data = pd.read_csv('scores.csv')
# Step 3: Convert the 'Date' column to datetime format
data['Date'] = pd.to_datetime(data['Date'], format='%a, %b %d, %Y', errors='coerce')

# Step 4: Define a function to determine the season year
def determine_season_year(date):
    if pd.isna(date):
        return None
    if date.month >= 10:
        return date.year + 1
    else:
        return date.year

# Step 5: Apply the function to create the 'Year' column
data['Year'] = data['Date'].apply(determine_season_year)
data.drop(columns=['Notes'], inplace=True)

data.to_csv("data.csv")

from bs4 import BeautifulSoup
import pandas as pd
import requests

def scrape_NBA_advanced_stats(url):
    # Send a GET request to the URL
    response = requests.get(url)
    # Check if the request was successful
    if response.status_code == 200:
        # Use BeautifulSoup to parse the HTML content
        soup = BeautifulSoup(response.content, 'html.parser')
        # Find the table by ID
        table = soup.find('table', {'id': 'advanced-team'})
        # Extract the column headers
        headers = [th.getText() for th in table.find_all('tr', limit=2)[1].find_all('th')]
        # Extract the rows from the table
        rows = table.find_all('tr')[2:]
        # Extract the data from each row
        data = [[td.getText() for td in row.find_all('td')] for row in rows if row.find('td')]
        # Create a DataFrame using the headers and the data
        df = pd.DataFrame(data, columns=headers[1:])  # Adjust the slicing based on your headers
        return df
    else:
        print("Failed to retrieve the page")
        return None

# Example usage
url = 'https://www.basketball-reference.com/leagues/NBA_2011.html'
df = scrape_NBA_advanced_stats(url)
df.head()  # Display the first few rows of the DataFrame


from time import sleep

def scrape_NBA_combined_advanced_stats(start_year, end_year, skip_years):
    all_data_frames = []  # List to store each year's DataFrame

    for year in range(start_year, end_year + 1):
        if year in skip_years:
            print(f"Skipping year {year}")
            continue  # Skip the years that are in the skip_years list

        print(f"Processing year {year}...")
        # Dynamically build the URL for each year
        url = f'https://www.basketball-reference.com/leagues/NBA_{year}.html'
        
        # Use the existing function to scrape the table
        df = scrape_NBA_advanced_stats(url)

        # Check if the DataFrame is not empty
        if df is not None and not df.empty:
            # Add a column to the DataFrame for the year
            df['Year'] = year
            # Append the DataFrame to the list
            all_data_frames.append(df)
        else:
            print(f"Could not retrieve data for {year}")

        # Be respectful to the server; don't send requests too quickly
        sleep(2)

    # Combine all DataFrames into one
    combined_df = pd.concat(all_data_frames, ignore_index=True)
    
    return combined_df
#2000, 2005, 2006,
# Example usage:
skip_years = [2000, 2005, 2006, 2012, 2020, 2021]
combined_data = scrape_NBA_combined_advanced_stats(2011, 2024, skip_years)
#combined_data = pd.read_csv("mergeddata.csv")
# Now you have a single DataFrame with all the data
# You can save this to a CSV file
#combined_data.to_csv("NBA_advanced_stats_combined.csv", index=False)
#print("Saved combined data to NBA_advanced_stats_combined.csv")

nba_stats_no_avg = combined_data[~combined_data['Team'].str.contains('League Average', na=False)]
# Remove asterisk from the 'Team' column values
nba_stats_no_avg['Team'] = nba_stats_no_avg['Team'].str.replace('*', '', regex=False)

# Display the DataFrame to verify the changes
df = nba_stats_no_avg
df.columns = ['Team', 'Age', 'W', 'L', 'PW', 'PL', 'MOV', 'SOS', 'SRS', 'ORtg', 'DRtg', 'NRtg', 
              'Pace', 'FTr', '3PAr', 'TS%', '', 'eFG%', 'TOV%', 'ORB%', 'FT/FGA', '', 
              'deFG%', 'dTOV%', 'DRB%', 'dFT/FGA', '', 'Arena', 'Attend.', 'Attend./G', 'Year']

# Display the updated column names to verify the changes
df.to_csv("stats.csv")
# Reading the CSV files into DataFrames
dfgames = pd.read_csv("data.csv")
dfstats = pd.read_csv("stats.csv")

# Renaming columns for clarity in the stats dataset
dfstats.rename(columns={'Team': 'Team Name', 'Year': 'Stats Year'}, inplace=True)

# Merging the games dataset with the stats dataset for the visitor team
dfgames_stats_visitor = pd.merge(dfgames, dfstats, left_on=['Visitor/Neutral', 'Year'], 
                                 right_on=['Team Name', 'Stats Year'], how='left')

# Renaming columns to reflect they are for the visitor team
dfgames_stats_visitor.rename(columns=lambda x: 'Away ' + x if x in dfstats.columns else x, inplace=True)

# Merging the updated games dataset with the stats dataset for the home team
dfgames_stats_combined = pd.merge(dfgames_stats_visitor, dfstats, left_on=['Home/Neutral', 'Year'], 
                                  right_on=['Team Name', 'Stats Year'], how='left')

# Renaming columns to reflect they are for the home team
dfgames_stats_combined.rename(columns=lambda x: 'Home ' + x if x in dfstats.columns else x, inplace=True)

# Display the first few rows of the combined DataFrame
dfgames_stats_combined.head()
dfgames_stats_combined = dfgames_stats_combined.loc[:, ~dfgames_stats_combined.columns.str.contains('Unnamed')]
dfgames_stats_combined.columns.tolist()
columns_to_remove = [
    'Arena_y', 'Attend._y', 'Away Attend./G', 'Away Stats Year',
    'Home Arena', 'Home Attend.', 'Home Attend./G', 'Home Stats Year', 'Home Team Name', 'Away Team Name', 'Away Age', 'Home Age'
]

# Removing the specified columns
dfgames_stats_combined = dfgames_stats_combined.drop(columns=columns_to_remove)
# Renaming columns 'Attend._x' to 'attendance' and 'Arena_x' to 'arena'
dfgames_stats_combined = dfgames_stats_combined.rename(columns={'Attend._x': 'Attendance', 'Arena_x': 'Arena', 'Visitor/Neutral': 'Away', 'Home/Neutral': 'Home', 'Visitor PTS': 'Away PTS', 'Year': 'Season Year'})

# Displaying the first few rows of the updated DataFrame
dfgames_stats_combined['Winner'] = dfgames_stats_combined.apply(
    lambda row: row['Away'] if row['Away PTS'] > row['Home PTS'] else row['Home'], axis=1
)

dfgames_stats_combined.to_csv("dfgames_stats_combined.csv")


dfgames_stats_combinedtest = dfgames_stats_combined.dropna(subset=['Home PTS', 'Away PTS'], how='all')
dfgames_stats_combinedtest.to_csv("dfgames_stats_combinedtest.csv")
dfgames_stats_combinedtest.tail(30)
dfgames_stats_combinedtrain = dfgames_stats_combined[
    (dfgames_stats_combined['Home PTS'].isna() & dfgames_stats_combined['Away PTS'].isna()) & 
    (dfgames_stats_combined['Season Year'] == 2024)
]

# Save the new dataset to a CSV file
dfgames_stats_combinedtrain.to_csv("dfgames_stats_combinedtrain.csv", index=False)
dfgames_stats_combinedtrain.head(30)

import pandas as pd
from sklearn.impute import SimpleImputer
from sklearn.feature_selection import SelectKBest, f_classif
from sklearn.preprocessing import StandardScaler
from sklearn.model_selection import train_test_split
import numpy as np
import tensorflow as tf
from tensorflow.keras.models import Sequential
from tensorflow.keras.layers import Dense
from tensorflow.keras.optimizers import Adam
from tensorflow.keras.callbacks import EarlyStopping

# Load the dataset
df = pd.read_csv("dfgames_stats_combinedtest.csv")
df = df[df['Season Year'] >= 2011]
df = df.dropna(subset=['Home PTS', 'Away PTS'], how='all')

# Create the 'Target' variable
df['Target'] = (df['Winner'] == df['Home']).astype(int)

# Exclude 'Home PTS' and 'Away PTS' from features
features_to_exclude = ['Home PTS', 'Away PTS', 'Target']
numeric_features = df.select_dtypes(include=['number']).drop(columns=features_to_exclude)

# Handle NaN values
imputer = SimpleImputer(strategy='mean')
X_imputed = imputer.fit_transform(numeric_features)

# Selecting the top features using SelectKBest
selector = SelectKBest(f_classif, k=14)  # Use 'all' to select all features for now
X_selected = selector.fit_transform(X_imputed, df['Target'])

# Get the names of the selected features
selected_features = numeric_features.columns[selector.get_support()]

# Standardize the data
scaler = StandardScaler()
X_selected_final_scaled = scaler.fit_transform(X_selected)

# Split the data into training and testing sets
X_train, X_test, y_train, y_test = train_test_split(X_selected_final_scaled, df['Target'], test_size=0.2, random_state=42)

# Neural Network Model
def create_model(input_dim, learning_rate=0.001):
    model = Sequential([
        Dense(64, input_dim=input_dim, activation='relu'),  # Input layer + hidden layer
        Dense(32, activation='relu'),  # Another hidden layer
        Dense(1, activation='sigmoid')  # Output layer
    ])
    
    model.compile(optimizer=Adam(learning_rate=learning_rate), loss='binary_crossentropy', metrics=['accuracy'])
    return model

# Train and evaluate the model
def train_and_evaluate_model(X_train, y_train, X_test, y_test, epochs=100, batch_size=32):
    early_stopping = EarlyStopping(monitor='val_loss', patience=10, restore_best_weights=True)
    input_dim = X_train.shape[1]  # Number of features
    model = create_model(input_dim)
    
    history = model.fit(X_train, y_train, epochs=epochs, batch_size=batch_size, validation_split=0.2, callbacks=[early_stopping], verbose=0)
    
    # Evaluate the model on the test set
    loss, accuracy = model.evaluate(X_test, y_test, verbose=0)
    return model, accuracy  # Return the model as well

# Train the model and evaluate it
model, accuracy = train_and_evaluate_model(X_train, y_train, X_test, y_test)
print(f"Test Accuracy: {accuracy*100:.2f}%")

# Preprocess the entire dataset
X_full_imputed = imputer.transform(numeric_features)  # Impute missing values
X_full_selected = selector.transform(X_full_imputed)  # Select features
X_full_scaled = scaler.transform(X_full_selected)  # Scale features

# Use the model to predict outcomes for the entire dataset
predicted_probabilities = model.predict(X_full_scaled)

# Convert probabilities to binary outcomes (1 if probability > 0.5, else 0)
predicted_outcomes = (predicted_probabilities > 0.5).astype(int)

# Create the "Predicted Winner" column based on predicted outcomes
# If predicted outcome is 1, the home team wins, otherwise the visitor team wins
df['Predicted Winner'] = np.where(predicted_outcomes.flatten() == 1, df['Home'], df['Away'])
df.tail(30)

# Load the dataset for future games
future_games_df = pd.read_csv("dfgames_stats_combinedtrain.csv")
future_games_df = future_games_df.drop(columns=['Winner'])


future_games_selected_features = future_games_df[selected_features]

# Impute missing values using the fitted imputer from the training

# Since we're directly using the selected features, we skip the feature selection step
# Scale the selected features using the fitted scaler from the training
X_future_scaled = scaler.transform(future_games_selected_features)

# Use the trained model to predict outcomes for future games
predicted_probabilities_future = model.predict(X_future_scaled)

# Convert probabilities to binary outcomes (1 if probability > 0.5, else 0)
predicted_outcomes_future = (predicted_probabilities_future > 0.5).astype(int)

# Create the "Predicted Winner" column based on predicted outcomes
# If predicted outcome is 1, the home team wins, otherwise the away team wins
future_games_df['Predicted Winner'] = np.where(predicted_outcomes_future.flatten() == 1, future_games_df['Home'], future_games_df['Away'])

# Display the future games dataset with the 'Predicted Winner' column
future_games_df[['Date', 'Home', 'Away', 'Predicted Winner']].head(30)
from datetime import datetime

future_games_df['Date'] = pd.to_datetime(future_games_df['Date'])

# Filter the DataFrame for rows where the 'Date' column is the current date
current_date = datetime.now().date()  # Get the current date
games_today_df = future_games_df[future_games_df['Date'].dt.date == current_date]
games_today_df[['Date', 'Home', 'Away', 'Predicted Winner']].head(30)

C:\Users\chris\AppData\Local\Temp\ipykernel_32644\1575566929.py:41: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  final_df = final_df.append(data_dict, ignore_index=True)
C:\Users\chris\AppData\Local\Temp\ipykernel_32644\1575566929.py:41: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  final_df = final_df.append(data_dict, ignore_index=True)
C:\Users\chris\AppData\Local\Temp\ipykernel_32644\1575566929.py:41: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  final_df = final_df.append(data_dict, ignore_index=True)
C:\Users\chris\AppData\Local\Temp\ipykernel_32644\1575566929.py:41: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  final_df = final_

C:\Users\chris\AppData\Local\Temp\ipykernel_32644\1575566929.py:41: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  final_df = final_df.append(data_dict, ignore_index=True)
C:\Users\chris\AppData\Local\Temp\ipykernel_32644\1575566929.py:41: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  final_df = final_df.append(data_dict, ignore_index=True)
C:\Users\chris\AppData\Local\Temp\ipykernel_32644\1575566929.py:41: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  final_df = final_df.append(data_dict, ignore_index=True)
C:\Users\chris\AppData\Local\Temp\ipykernel_32644\1575566929.py:41: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  final_df = final_

C:\Users\chris\AppData\Local\Temp\ipykernel_32644\1575566929.py:41: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  final_df = final_df.append(data_dict, ignore_index=True)
C:\Users\chris\AppData\Local\Temp\ipykernel_32644\1575566929.py:41: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  final_df = final_df.append(data_dict, ignore_index=True)
C:\Users\chris\AppData\Local\Temp\ipykernel_32644\1575566929.py:41: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  final_df = final_df.append(data_dict, ignore_index=True)
C:\Users\chris\AppData\Local\Temp\ipykernel_32644\1575566929.py:41: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  final_df = final_

C:\Users\chris\AppData\Local\Temp\ipykernel_32644\1575566929.py:41: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  final_df = final_df.append(data_dict, ignore_index=True)
C:\Users\chris\AppData\Local\Temp\ipykernel_32644\1575566929.py:41: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  final_df = final_df.append(data_dict, ignore_index=True)
C:\Users\chris\AppData\Local\Temp\ipykernel_32644\1575566929.py:41: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  final_df = final_df.append(data_dict, ignore_index=True)
C:\Users\chris\AppData\Local\Temp\ipykernel_32644\1575566929.py:41: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  final_df = final_

C:\Users\chris\AppData\Local\Temp\ipykernel_32644\1575566929.py:41: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  final_df = final_df.append(data_dict, ignore_index=True)
C:\Users\chris\AppData\Local\Temp\ipykernel_32644\1575566929.py:41: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  final_df = final_df.append(data_dict, ignore_index=True)
C:\Users\chris\AppData\Local\Temp\ipykernel_32644\1575566929.py:41: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  final_df = final_df.append(data_dict, ignore_index=True)
C:\Users\chris\AppData\Local\Temp\ipykernel_32644\1575566929.py:41: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  final_df = final_

...

Processing year 2011...
Skipping year 2012
Processing year 2013...
Processing year 2014...
Processing year 2015...
Processing year 2016...
Processing year 2017...
Processing year 2018...
Processing year 2019...
Skipping year 2020
Skipping year 2021
Processing year 2022...
Processing year 2023...
Processing year 2024...


C:\Users\chris\AppData\Local\Temp\ipykernel_32644\1575566929.py:163: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  nba_stats_no_avg['Team'] = nba_stats_no_avg['Team'].str.replace('*', '', regex=False)






Test Accuracy: 68.02%
9/9 [==============================] - 0s 2ms/step


C:\Users\chris\anaconda3\lib\site-packages\sklearn\base.py:486: UserWarning: X has feature names, but StandardScaler was fitted without feature names
  warnings.warn(


Date                   Home                    Away  \
0 2024-03-12        New York Knicks      Philadelphia 76ers   
1 2024-03-12      Memphis Grizzlies      Washington Wizards   
2 2024-03-12  Oklahoma City Thunder          Indiana Pacers   
3 2024-03-12      San Antonio Spurs         Houston Rockets   
4 2024-03-12              Utah Jazz          Boston Celtics   
5 2024-03-12   Los Angeles Clippers  Minnesota Timberwolves   
6 2024-03-12       Sacramento Kings         Milwaukee Bucks   

         Predicted Winner  
0      Philadelphia 76ers  
1       Memphis Grizzlies  
2   Oklahoma City Thunder  
3         Houston Rockets  
4          Boston Celtics  
5  Minnesota Timberwolves  
6         Milwaukee Bucks